In [ ]:
#You don't need to change anything in this block, although the modules need to be installed to run this notebook

#We import numpy to handle vectors and some math
import numpy as np

#We import pandas to create a data frame of the experiment data
#Such a table can later be used for plotting our results
import pandas as pd

# Import plotly, which is used for visualization
import plotly.express as px
import plotly.io as pio
pio.renderers.default = 'iframe'

In [ ]:
# generate N random particles in a 2d environment with a given pattern:
def generate_pattern(N):
    return np.random.rand(N, 2)

In [ ]:
# record data into dataframe (used for plotting)
def make_df(data, t, type_name):
    df = pd.DataFrame(data, columns=["x", "y"])
    df['t'] = t
    df['type'] = type_name
    df['pid'] = range(len(data))
    return df

In [ ]:
# forces between a pair of particles i, j
def force_ij(i, j, pattern, particles, k=0.3):
    dist = np.linalg.norm(pattern[i, :] - pattern[j, :])
    xi_minus_xj = particles[i, :] - particles[j, :]
    f = -k * (np.linalg.norm(xi_minus_xj) - dist) * xi_minus_xj
    return f

# force for particle i
def force_i(i, pattern, particles, k=0.3):
    f = np.array([0.0, 0.0])
    for j, _ in enumerate(particles):
        if j == i:
            continue
        f = f + force_ij(i, j, pattern, particles, k=k)
    return f

# forces for all particles
def force(pattern, particles, k=0.1):
    return np.array([force_i(i, pattern, particles, k=k) for i, _ in enumerate(particles)])


In [ ]:
# run an experiment with N random particles and a random pattern
l = []
data = []
N = 5
pattern = generate_pattern(N)
x = generate_pattern(N)
v = np.zeros_like(x)
for t in range(30):
    # record the current state at time t
    data.append(make_df(x, t, "particle"))
    data.append(make_df(pattern, t, "pattern"))
  
    # update v and x
    v = force(pattern, x, k=0.3) + 0.3 * v
    x = x + v
df = pd.concat(data)

# show the result
fig = px.scatter(df, x="x", y="y", color="pid", animation_frame="t", animation_group="pid", facet_col="type")
fig.update_layout(xaxis_range=(-0.5, 1.5), yaxis_range=(-0.5, 1.5), width=1600, height=800)
fig.update_traces(marker={"size": 12})
fig.show()